In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from lightkurve import KeplerTargetPixelFile
import csv
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")

/home/ubuntu/anaconda3/lib/python3.6/site-packages/matplotlib/__init__.py:962: UserWarning: Duplicate key in file "/home/ubuntu/.config/matplotlib/matplotlibrc", line #2
  (fname, cnt))
/home/ubuntu/anaconda3/lib/python3.6/site-packages/matplotlib/__init__.py:962: UserWarning: Duplicate key in file "/home/ubuntu/.config/matplotlib/matplotlibrc", line #3
  (fname, cnt))


In [2]:
# Need to get data in the proper format

# to get eaten by tensorflow, we need to get everything into a Vector. 
# Must create a test set and a training set.

# I want the  flux in a list per star. (Need to check if its ok to have floats as these values)
# also need to organize it into batches of abt 100 or so so that the model can backpropegate
# index = kepid
# columns = fluxes

# then, I need the results in list form. They must be numerical answers, not boolean, not categorical.
# index = kepid
# 1 = exoplanet
# 2 = not

---
# Create Pandas DataFrame of target values from NASAEA csv file

In [5]:
# create dy
# pandas dataframe that will contain all the target values
# we want it to be formatted as a vector
dy = pd.read_csv('/home/ubuntu/KEPLER/cumulative.csv', usecols=['kepid', 'Disposition'],   
                      sep=',', 
                      index_col=None, 
                      parse_dates=True, 
                      encoding=None, 
                      tupleize_cols=None, 
                      infer_datetime_format=False)

### Encode target values: "Candidate" = 1, all others = 0 

In [7]:
# values within dy need to be numbers
# 0 = not an exoplanet
# 1 = candidate

for i in tqdm(range(9564)):
    if (dy["Disposition"][i] == "CANDIDATE"):
        dy["Disposition"][i] = 1
    else:
        dy["Disposition"][i] = 0

100%|██████████| 9564/9564 [08:33<00:00, 18.61it/s]


### Create starlist: list of Kepler ID's

In [6]:
starlist = []
for i in range(9564):
    starlist.append(dy['kepid'][i])

### Define TFsinglestarpipe:
- function that takes in a KeplerID, returns a 1D vector (np.array) of fluxes

In [10]:
def TFsinglestarpipe(kepid):
    try:
        tpf = KeplerTargetPixelFile.from_archive(kepid, quarter=1)  
        lc = tpf.to_lightcurve(aperture_mask=tpf.pipeline_mask)
        flat, trend = lc.flatten(window_length=301, return_trend=True)
        df = flat.to_pandas()
    
        df["KeplerID"] = kepid
        df = df.drop(columns = ['time', 
                        'flux_err', 
                        'quality', 
                        'centroid_row', 
                        'centroid_col',
                        'KeplerID'], axis=1)
    
        df = df.reset_index(drop=True)
        df.index.names = [kepid]
    
        flux = df['flux']
        array = list(flux)
        return array
    except:
        return None

# Create xtrain and ytrain

In [8]:
xtrain = []
ytrain = []

for i in tqdm(range(7000)):
    if TFsinglestarpipe(starlist[i]):
        xtrain.append(TFsinglestarpipe(starlist[i]))
        ytrain.append(dy['Disposition'][i])
    else:
        pass

X_train = np.array(xtrain)
Y_train = np.array(ytrain)

  0%|          | 0/7000 [00:00<?, ?it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr010797460_lc_Q011111111111111111/kplr010797460-2009166043257_lpd-targ.fits.gz with expected size 535639. [astroquery.query]


  0%|          | 1/7000 [00:00<1:34:05,  1.24it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr010797460_lc_Q011111111111111111/kplr010797460-2009166043257_lpd-targ.fits.gz with expected size 535639. [astroquery.query]
INFO: Found cached file ./mastDownload/Kepler/kplr010797460_lc_Q011111111111111111/kplr010797460-2009166043257_lpd-targ.fits.gz with expected size 535639. [astroquery.query]


  0%|          | 2/7000 [00:01<1:23:29,  1.40it/s]

...

100%|█████████▉| 6998/7000 [1:19:17<00:01,  1.47it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr005385269_lc_Q011111111111111111/kplr005385269-2009166043257_lpd-targ.fits.gz with expected size 750737. [astroquery.query]


100%|█████████▉| 6999/7000 [1:19:17<00:00,  1.47it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr005385269_lc_Q011111111111111111/kplr005385269-2009166043257_lpd-targ.fits.gz with expected size 750737. [astroquery.query]


100%|██████████| 7000/7000 [1:19:17<00:00,  1.47it/s]


# Create xtest and ytest

In [ ]:
xtest = []
ytest = []

for i in tqdm(range(2564)):
    if TFsinglestarpipe(starlist[i+7000]):
        xtest.append(TFsinglestarpipe(starlist[i+7000]))
        ytest.append(dy['Disposition'][i+7000])
    else:
        pass

X_test = np.array(xtest)
Y_test = np.array(ytest)

  0%|          | 1/2564 [00:00<09:02,  4.72it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr005385773_lc_Q011111111111111111/kplr005385773-2009166043257_lpd-targ.fits.gz with expected size 626733. [astroquery.query]


  0%|          | 2/2564 [00:01<31:49,  1.34it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr005385773_lc_Q011111111111111111/kplr005385773-2009166043257_lpd-targ.fits.gz with expected size 626733. [astroquery.query]
INFO: Found cached file ./mastDownload/Kepler/kplr005386163_lc_Q111111111111111111/kplr005386163-2009166043257_lpd-targ.fits.gz with expected size 884730. [astroquery.query]


  0%|          | 3/2564 [00:02<30:51,  1.38it/s]

...

100%|█████████▉| 2552/2564 [26:57<00:07,  1.58it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr008560927_lc_Q111111111111111111/kplr008560927-2009166043257_lpd-targ.fits.gz with expected size 1013283. [astroquery.query]


100%|█████████▉| 2553/2564 [26:58<00:06,  1.58it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr008560927_lc_Q111111111111111111/kplr008560927-2009166043257_lpd-targ.fits.gz with expected size 1013283. [astroquery.query]


100%|█████████▉| 2557/2564 [26:58<00:04,  1.58it/s]

### Save all arrays

In [9]:
np.save('xtrainfile2', xtrain)
np.save('ytrainfile2', ytrain)

In [24]:
# pickle those np.arrays
np.save('xtestfile2', xtest)
np.save('ytestfile2', ytest)

In [26]:
# if you want to load any of those np.arrays back into the notebook... use this:
#x =np.load('xtrainfile.npy')

### Now start working in TensorFlow

In [ ]:
# Me trying to reformat the y vectors so they are either 0 or 0.5
# because apparently tensorboard won't take 1's

In [ ]:
# values within dy need to be numbers
# 0 = not an exoplanet
# 0.5 = candidate

for i in tqdm(range(9564)):
    if (dy["Disposition"][i] == "CANDIDATE"):
        dy["Disposition"][i] = 0.5
    else:
        dy["Disposition"][i] = 0

In [13]:
ytrain = []
ytest = []

for i in tqdm(range(7000)):
    if TFsinglestarpipe(starlist[i]):
        ytrain.append(dy['Disposition'][i])
    else:
        pass
    
for i in tqdm(range(2564)):
    if TFsinglestarpipe(starlist[i+7000]):
        ytest.append(dy['Disposition'][i+7000])
    else:
        pass

Y_train = np.array(ytrain)
Y_test = np.array(ytest)

  0%|          | 1/7000 [00:00<39:25,  2.96it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr010797460_lc_Q011111111111111111/kplr010797460-2009166043257_lpd-targ.fits.gz with expected size 535639. [astroquery.query]


  0%|          | 2/7000 [00:00<38:29,  3.03it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr010797460_lc_Q011111111111111111/kplr010797460-2009166043257_lpd-targ.fits.gz with expected size 535639. [astroquery.query]


  0%|          | 3/7000 [00:01<42:52,  2.72it/s]

...

INFO: Found cached file ./mastDownload/Kepler/kplr010128825_lc_Q011111111111111111/kplr010128825-2009166043257_lpd-targ.fits.gz with expected size 588044. [astroquery.query]


100%|█████████▉| 2563/2564 [13:33<00:00,  3.15it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr010147276_lc_Q011111111111111111/kplr010147276-2009166043257_lpd-targ.fits.gz with expected size 496203. [astroquery.query]


100%|██████████| 2564/2564 [13:33<00:00,  3.15it/s]

INFO: Found cached file ./mastDownload/Kepler/kplr010156110_lc_Q011111101110111011/kplr010156110-2009166043257_lpd-targ.fits.gz with expected size 620884. [astroquery.query]


In [14]:
np.save('ytestfile3',Y_test)
np.save('ytrainfile3', Y_train)